In [241]:
from sklearn.ensemble import VotingClassifier
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split, GridSearchCV, StratifiedKFold
from sklearn.preprocessing import MinMaxScaler, StandardScaler, OneHotEncoder
from sklearn.compose import make_column_transformer, make_column_selector
from sklearn.tree import DecisionTreeClassifier, DecisionTreeRegressor
from sklearn.naive_bayes import GaussianNB
from sklearn.metrics import accuracy_score, roc_auc_score, r2_score
from sklearn.linear_model import LogisticRegression, LinearRegression, ElasticNet
from sklearn.pipeline import Pipeline
from sklearn.neighbors import KNeighborsRegressor

# voting classifier

In [64]:
cancer

Code  Clump  UniCell_Size  Uni_CellShape  MargAdh  SEpith  BareN  \
0       61634      5             4              3        1       2      2   
1       63375      9             1              2        6       4     10   
2       76389     10             4              7        2       2      8   
3       95719      6            10             10       10       8     10   
4      128059      1             1              1        1       2      5   
..        ...    ...           ...            ...      ...     ...    ...   
694   1369821     10            10             10       10       5     10   
695   1371026      5            10             10       10       4     10   
696   1371920      5             1              1        1       2      1   
697   8233704      4             1              1        1       1      1   
698  13454352      1             1              3        1       2      1   

     BChromatin  NoemN  Mitoses      Class  
0             2      3        1     Benign  
1             7      7        2  Malignant  
2             6      1        1  Malignant  
3             7     10        7  Malignant  
4             5      1        1     Benign  
..          ...    ...      ...        ...  
694          10     10        7  Malignant  
695           5      6        3  Malignant  
696           3      2        1     Benign  
697           2      1        1     Benign  
698           2      1        1     Benign  

[699 rows x 11 columns]

In [66]:
cancer = pd.read_csv("Cases/Wisconsin/BreastCancer.csv", index_col = 0)
X = cancer.drop("Class", axis =1)
y = cancer.Class

In [68]:
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state = 24, test_size = .3, stratify = y)

In [70]:
dtc = DecisionTreeClassifier(random_state = 24)
lr = LogisticRegression(random_state = 24)
nb = GaussianNB()
voting = VotingClassifier([('DT', dtc), ('LR', lr), ("NB", nb)])
voting.fit(X_train, y_train)
y_pred = voting.predict(X_test)
print(accuracy_score(y_test, y_pred))

0.9666666666666667


### using `voting = soft`

In [73]:
voting = VotingClassifier([('DT', dtc), ('LR', lr), ("NB", nb)], voting = 'soft')
voting.fit(X_train, y_train)
y_pred_proba = voting.predict_proba(X_test)[:,1]
print(roc_auc_score(y_test, y_pred_proba))

0.9951690821256038


In [75]:
dtc = DecisionTreeClassifier(random_state = 24, max_depth = 3)
voting = VotingClassifier([('DT', dtc), ('LR', lr), ("NB", nb)], voting = 'soft')
voting.fit(X_train, y_train)
y_pred_proba = voting.predict_proba(X_test)[:,1]
print(roc_auc_score(y_test, y_pred_proba))

0.9915458937198067


### using gcv

In [101]:
dtc.get_params()
params = {'DT__max_depth':[None, 2, 3], 'DT__min_samples_split': [2, 10, 20], 'DT__min_samples_leaf' :[1, 10 , 20], 'LR__C': np.linspace(0.001, 3, 5), 'NB__var_smoothing': np.linspace(1e-09, 1e-4, 4)}
gcv = GridSearchCV(voting, param_grid = params, cv = StratifiedKFold(n_splits = 5, shuffle = True, random_state = 24), verbose = 2, scoring = 'roc_auc')
gcv.fit(X, y)

Fitting 5 folds for each of 540 candidates, totalling 2700 fits
[CV] END DT__max_depth=None, DT__min_samples_leaf=1, DT__min_samples_split=2, LR__C=0.001, NB__var_smoothing=1e-09; total time=   0.0s
[CV] END DT__max_depth=None, DT__min_samples_leaf=1, DT__min_samples_split=2, LR__C=0.001, NB__var_smoothing=1e-09; total time=   0.0s
[CV] END DT__max_depth=None, DT__min_samples_leaf=1, DT__min_samples_split=2, LR__C=0.001, NB__var_smoothing=1e-09; total time=   0.0s
[CV] END DT__max_depth=None, DT__min_samples_leaf=1, DT__min_samples_split=2, LR__C=0.001, NB__var_smoothing=1e-09; total time=   0.0s
[CV] END DT__max_depth=None, DT__min_samples_leaf=1, DT__min_samples_split=2, LR__C=0.001, NB__var_smoothing=1e-09; total time=   0.0s
[CV] END DT__max_depth=None, DT__min_samples_leaf=1, DT__min_samples_split=2, LR__C=0.001, NB__var_smoothing=3.3334e-05; total time=   0.0s
[CV] END DT__max_depth=None, DT__min_samples_leaf=1, DT__min_samples_split=2, LR__C=0.001, NB__var_smoothing=3.3334e-05; 

GridSearchCV(cv=StratifiedKFold(n_splits=5, random_state=24, shuffle=True),
             estimator=VotingClassifier(estimators=[('DT',
                                                     DecisionTreeClassifier(max_depth=3,
                                                                            random_state=24)),
                                                    ('LR',
                                                     LogisticRegression(random_state=24)),
                                                    ('NB', GaussianNB())],
                                        voting='soft'),
             param_grid={'DT__max_depth': [None, 2, 3],
                         'DT__min_samples_leaf': [1, 10, 20],
                         'DT__min_samples_split': [2, 10, 20],
                         'LR__C': array([1.00000e-03, 7.50750e-01, 1.50050e+00, 2.25025e+00, 3.00000e+00]),
                         'NB__var_smoothing': array([1.0000e-09, 3.3334e-05, 6.6667e-05, 1.0000e-04])},
             scoring='roc_auc', verbose=2)

In [103]:
print(gcv.best_params_)
gcv.best_score_

{'DT__max_depth': None, 'DT__min_samples_leaf': 1, 'DT__min_samples_split': 2, 'LR__C': 0.001, 'NB__var_smoothing': 1e-09}


0.9937986416496842

## on hr dataset

In [108]:
hr = pd.read_csv("Cases/human-resources-analytics/HR_comma_sep.csv")

In [110]:
hr.head()

satisfaction_level  last_evaluation  number_project  average_montly_hours  \
0                0.38             0.53               2                   157   
1                0.80             0.86               5                   262   
2                0.10             0.77               6                   247   
3                0.92             0.85               5                   259   
4                0.89             1.00               5                   224   

   time_spend_company  Work_accident  left  promotion_last_5years Department  \
0                   3              0     1                      0      sales   
1                   6              0     1                      0      sales   
2                   4              0     1                      0      sales   
3                   5              0     1                      0      sales   
4                   5              0     1                      0      sales   

   salary  
0     low  
1  medium  
2     low  
3     low  
4     low

In [116]:
y = hr.left
X = hr.drop('left', axis=1)

In [150]:
ohe =OneHotEncoder(drop = 'first', handle_unknown='ignore') # In long run we dont do drop first. If we get unknown category it would be 0.
ct = make_column_transformer(('passthrough', make_column_selector(dtype_exclude= object)), (ohe, make_column_selector(dtype_include = object)))

In [166]:
dtc = DecisionTreeClassifier(random_state=24)
lr = LogisticRegression(random_state = 24)
nb = GaussianNB()
voting = VotingClassifier([('DTC',dtc),('LR',lr),('NB',nb)])
pipe = Pipeline([('CT', ct), ('VOT', voting)])
params = {'VOT__DTC__max_depth':[None, 2, 3], 'VOT__DTC__min_samples_split': [2, 10, 20], 'VOT__DTC__min_samples_leaf' :[1, 10 , 20] 'VOT__LR__C': np.linspace(0.001, 3, 2)}
gcv = GridSearchCV(pipe, param_grid = params, scoring = 'roc_auc', cv = StratifiedKFold(n_splits = 5, shuffle = True, random_state = 24), verbose = 2)

In [168]:
gcv.fit(X, y)

Fitting 5 folds for each of 540 candidates, totalling 2700 fits


C:\Users\DAI.STUDENTSDC\AppData\Local\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:469: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
C:\Users\DAI.STUDENTSDC\AppData\Local\anaconda3\Lib\site-packages\sklearn\model_selection\_validation.py:982: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\DAI.STUDENTSDC\AppData\Local\anaconda3\Lib\site-packages\sklearn\model_selection\_validation.py", line 971, in _score
    scores = scorer(estimator, X_test, y_test, **score_params)
 

[CV] END VOT__DTC__max_depth=None, VOT__DTC__min_samples_leaf=1, VOT__DTC__min_samples_split=2, VOT__LR__C=0.001, VOT__NB__var_smoothing=1e-09; total time=   0.1s


C:\Users\DAI.STUDENTSDC\AppData\Local\anaconda3\Lib\site-packages\sklearn\model_selection\_validation.py:982: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\DAI.STUDENTSDC\AppData\Local\anaconda3\Lib\site-packages\sklearn\model_selection\_validation.py", line 971, in _score
    scores = scorer(estimator, X_test, y_test, **score_params)
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "C:\Users\DAI.STUDENTSDC\AppData\Local\anaconda3\Lib\site-packages\sklearn\metrics\_scorer.py", line 279, in __call__
    return self._score(partial(_cached_call, None), estimator, X, y_true, **_kwargs)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "C:\Users\DAI.STUDENTSDC\AppData\Local\anaconda3\Lib\site-packages\sklearn\metrics\_scorer.py", line 370, in _score
    response_method = _check_response_method(estimator, s

[CV] END VOT__DTC__max_depth=None, VOT__DTC__min_samples_leaf=1, VOT__DTC__min_samples_split=2, VOT__LR__C=0.001, VOT__NB__var_smoothing=1e-09; total time=   0.1s


...

C:\Users\DAI.STUDENTSDC\AppData\Local\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:469: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
C:\Users\DAI.STUDENTSDC\AppData\Local\anaconda3\Lib\site-packages\sklearn\model_selection\_validation.py:982: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\DAI.STUDENTSDC\AppData\Local\anaconda3\Lib\site-packages\sklearn\model_selection\_validation.py", line 971, in _score
    scores = scorer(estimator, X_test, y_test, **score_params)
 

[CV] END VOT__DTC__max_depth=3, VOT__DTC__min_samples_leaf=20, VOT__DTC__min_samples_split=20, VOT__LR__C=3.0, VOT__NB__var_smoothing=0.0001; total time=   0.1s


C:\Users\DAI.STUDENTSDC\AppData\Local\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:469: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
C:\Users\DAI.STUDENTSDC\AppData\Local\anaconda3\Lib\site-packages\sklearn\model_selection\_validation.py:982: UserWarning: Scoring failed. The score on this train-test partition for these parameters will be set to nan. Details: 
Traceback (most recent call last):
  File "C:\Users\DAI.STUDENTSDC\AppData\Local\anaconda3\Lib\site-packages\sklearn\model_selection\_validation.py", line 971, in _score
    scores = scorer(estimator, X_test, y_test, **score_params)
 

[CV] END VOT__DTC__max_depth=3, VOT__DTC__min_samples_leaf=20, VOT__DTC__min_samples_split=20, VOT__LR__C=3.0, VOT__NB__var_smoothing=0.0001; total time=   0.1s


GridSearchCV(cv=StratifiedKFold(n_splits=5, random_state=24, shuffle=True),
             estimator=Pipeline(steps=[('CT',
                                        ColumnTransformer(transformers=[('passthrough',
                                                                         'passthrough',
                                                                         <sklearn.compose._column_transformer.make_column_selector object at 0x000002B3EC18D400>),
                                                                        ('onehotencoder',
                                                                         OneHotEncoder(drop='first',
                                                                                       handle_unknown='ignore'),
                                                                         <sklearn.compose._column_tran...
                                                                      LogisticRegression(random_state=24)),
                                                                     ('NB',
                                                                      GaussianNB())]))]),
             param_grid={'VOT__DTC__max_depth': [None, 2, 3],
                         'VOT__DTC__min_samples_leaf': [1, 10, 20],
                         'VOT__DTC__min_samples_split': [2, 10, 20],
                         'VOT__LR__C': array([1.00000e-03, 7.50750e-01, 1.50050e+00, 2.25025e+00, 3.00000e+00]),
                         'VOT__NB__var_smoothing': array([1.0000e-09, 3.3334e-05, 6.6667e-05, 1.0000e-04])},
             scoring='roc_auc', verbose=2)

In [169]:
gcv.best_score_

nan

# votingRegressor

In [175]:
from sklearn.ensemble import VotingRegressor

In [295]:
df = pd.read_csv("Cases/Concrete Strength/Concrete_Data.csv")
X = df.drop("Strength", axis = 1)
y = df.Strength
df.head()

Cement  Blast  Fly  Water  Superplasticizer  Coarse   Fine  Age  Strength
0   540.0    0.0  0.0  162.0               2.5  1040.0  676.0   28     79.99
1   540.0    0.0  0.0  162.0               2.5  1055.0  676.0   28     61.89
2   332.5  142.5  0.0  228.0               0.0   932.0  594.0  270     40.27
3   332.5  142.5  0.0  228.0               0.0   932.0  594.0  365     41.05
4   198.6  132.4  0.0  192.0               0.0   978.4  825.5  360     44.30

In [271]:
lr = LinearRegression()
knnr = KNeighborsRegressor()
dtr = DecisionTreeRegressor(random_state = 24)
el = ElasticNet()

In [273]:
X_test, X_train, y_test, y_train = train_test_split(X, y, test_size = .3, random_state = 24)
# X_test_c = ct.fit_transform(X_test)
# X_train_c = ct.fit_transform(X_train)

In [275]:
dtr.fit(X_train, y_train)
y_pred = dtr.predict(X_test)
r2_score(y_test, y_pred)

0.7301200068362702

In [276]:
lr.fit(X_train, y_train)
y_pred = lr.predict(X_test)
r2_score(y_test, y_pred)

0.6050202059767258

In [279]:
el.fit(X_train, y_train)
y_pred = el.predict(X_test)
r2_score(y_test, y_pred)

0.6057812886020282

In [280]:
dtr.fit(X_train, y_train)
y_pred = dtr.predict(X_test)
r2_score(y_test, y_pred)

0.7301200068362702

In [281]:
voting = VotingRegressor([('DT', dtr), ('LR', lr), ('KNNR', knnr)])
voting.fit(X_train, y_train)
y_pred = voting.predict(X_test)
r2_score(y_test, y_pred)

0.7414015687097554

## weighted average

In [286]:
voting = VotingRegressor([('DT', dtr), ('LR', lr), ('KNNR', knnr), ('EL', el)], 
                        weights = [.6, .1, .2, .1]  )

In [287]:
voting = VotingRegressor([('DT', dtr), ('LR', lr), ('KNNR', knnr)])
voting.fit(X_train, y_train)
y_pred = voting.predict(X_test)
r2_score(y_test, y_pred)

0.7414015687097554

In [299]:
dtr1 = DecisionTreeRegressor(random_state=24, max_depth= None)
dtr2 = DecisionTreeRegressor(random_state=24, max_depth= 3)
dtr3 = DecisionTreeRegressor(random_state=24, max_depth= 4)
voting = VotingRegressor([('M1', dtr1), ('M2', dtr2), ('M3', dtr3)], weights = [0.7,0.15,0.15])
voting.fit(X_train, y_train)
y_pred= voting.predict(X_test)
r2_score(y_test, y_pred)

0.741739583936627

## on other dataset 
insurance

In [303]:
med = pd.read_csv("Cases/Medical Cost Personal/insurance.csv")
med.head()

age     sex     bmi  children smoker     region      charges
0   19  female  27.900         0    yes  southwest  16884.92400
1   18    male  33.770         1     no  southeast   1725.55230
2   28    male  33.000         3     no  southeast   4449.46200
3   33    male  22.705         0     no  northwest  21984.47061
4   32    male  28.880         0     no  northwest   3866.85520

In [307]:
X = med.drop("charges", axis = 1)
y = med.charges

In [317]:
lr = LinearRegression()
knnr = KNeighborsRegressor()
dtr = DecisionTreeRegressor(random_state = 24)
el = ElasticNet()
ohe = OneHotEncoder(handle_unknown = 'ignore')
ct = make_column_transformer(('passthrough', make_column_selector(dtype_exclude= object)), (ohe, make_column_selector(dtype_include = object)))

In [319]:
X_test, X_train, y_test, y_train = train_test_split(X, y, test_size = .3, random_state = 24)

In [325]:
X_tst = ct.fit_transform(X_test)
X_trn = ct.fit_transform(X_train)

In [335]:
lr.fit(X_trn, y_train)
y_pred= lr.predict(X_tst)
r2lr = r2_score(y_test, y_pred)
print('r2Score: ',r2lr)

r2Score:  0.7299181963173813


In [339]:
el.fit(X_trn, y_train)
y_pred= el.predict(X_tst)
r2el = r2_score(y_test, y_pred)
print('r2Score: ',r2el)

r2Score:  0.5320576770059062


In [341]:
dtr.fit(X_trn, y_train)
y_pred= dtr.predict(X_tst)
r2dtr = r2_score(y_test, y_pred)
print('r2Score: ',r2dtr)

r2Score:  0.7473274980312878


In [355]:
voting = VotingRegressor([('LR', lr), ('EL',el), ('DTR', dtr)], weights=[800,400,800])
voting.fit(X_trn, y_train)
y_pred = voting.predict(X_tst)
r2vot = r2_score(y_test, y_pred)
print('r2Score: ',r2vot)

r2Score:  0.7954522949494457


In [4]:
pip install ydata_profiling

  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'done'
   ---------------------------------------- 0.0/390.6 kB ? eta -:--:--
   ------------ --------------------------- 122.9/390.6 kB 3.6 MB/s eta 0:00:01
   ---------------------------------------  389.1/390.6 kB 4.9 MB/s eta 0:00:01
   ---------------------------------------- 390.6/390.6 kB 4.0 MB/s eta 0:00:00
   ---------------------------------------- 0.0/296.5 kB ? eta -:--:--
   --------------------------------------- 296.5/296.5 kB 19.1 MB/s eta 0:00:00
   ---------------------------------------- 0.0/666.4 kB ? eta -:--:--
   --------------------------------------- 666.4/666.4 kB 14.0 MB/s eta 0:00:00
   ---------------------------------------- 0.0/104.8 kB ? eta -:--:--
   ---------------------------------------- 104.8/104.8 kB 5.9 MB/s eta 0:00:00
   ---------------------------------------- 0.0/301.4 kB ? eta -:--:--
   --------------------------------------- 301.4/301.4 kB 18.2 

In [12]:
from ydata_profiling import ProfileReport
import pandas as pd

In [20]:
profile = ProfileReport(df)

In [16]:
df = pd.read_csv('Datasets/bank.csv')

In [ ]:
profile.to_file("books_data.html")

In [ ]:
pip install ISLP